<a href="https://colab.research.google.com/github/abd11198/Camera-Based-AI-Detection-System/blob/main/Keys_Dectiction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!nvidia-smi

Thu Apr 10 17:33:35 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   60C    P8             11W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [ ]:
# Unzip images to a custom data folder
!unzip -q /content/data.zip -d /content/custom_data

In [ ]:
!wget -O /content/train_val_split.py https://raw.githubusercontent.com/EdjeElectronics/Train-and-Deploy-YOLO-Models/refs/heads/main/utils/train_val_split.py

# TO DO: Improve robustness of train_val_split.py script so it can handle nested data folders, etc
!python train_val_split.py --datapath="/content/custom_data" --train_pct=0.9

--2025-03-31 07:27:59--  https://raw.githubusercontent.com/EdjeElectronics/Train-and-Deploy-YOLO-Models/refs/heads/main/utils/train_val_split.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3203 (3.1K) [text/plain]
Saving to: ‘/content/train_val_split.py’

/content/train_val_ 100%[===================>]   3.13K  --.-KB/s    in 0s      

2025-03-31 07:27:59 (49.0 MB/s) - ‘/content/train_val_split.py’ saved [3203/3203]

Created folder at /content/data/train/images.
Created folder at /content/data/train/labels.
Created folder at /content/data/validation/images.
Created folder at /content/data/validation/labels.
Number of image files: 231
Number of annotation files: 231
Images moving to train: 207
Images moving to validation: 24


In [ ]:
!pip install ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 976.9/976.9 kB 52.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 112.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 81.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 53.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 60.5 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstal

In [ ]:
# Python function to automatically create data.yaml config file
# 1. Reads "classes.txt" file to get list of class names
# 2. Creates data dictionary with correct paths to folders, number of classes, and names of classes
# 3. Writes data in YAML format to data.yaml

import yaml
import os

def create_data_yaml(path_to_classes_txt, path_to_data_yaml):

  # Read class.txt to get class names
  if not os.path.exists(path_to_classes_txt):
    print(f'classes.txt file not found! Please create a classes.txt labelmap and move it to {path_to_classes_txt}')
    return
  with open(path_to_classes_txt, 'r') as f:
    classes = []
    for line in f.readlines():
      if len(line.strip()) == 0: continue
      classes.append(line.strip())
  number_of_classes = len(classes)

  # Create data dictionary
  data = {
      'path': '/content/data',
      'train': 'train/images',
      'val': 'validation/images',
      'nc': number_of_classes,
      'names': classes
  }

  # Write data to YAML file
  with open(path_to_data_yaml, 'w') as f:
    yaml.dump(data, f, sort_keys=False)
  print(f'Created config file at {path_to_data_yaml}')

  return

# Define path to classes.txt and run function
path_to_classes_txt = '/content/custom_data/classes.txt'
path_to_data_yaml = '/content/data.yaml'

create_data_yaml(path_to_classes_txt, path_to_data_yaml)

print('\nFile contents:\n')
!cat /content/data.yaml

Created config file at /content/data.yaml

File contents:

path: /content/data
train: train/images
val: validation/images
nc: 2
names:
- House_Key
- Work_Key


In [ ]:
!yolo detect train data=/content/data.yaml model=yolo11s.pt epochs=60 imgsz=640

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
100% 18.4M/18.4M [00:00<00:00, 65.2MB/s]
Ultralytics 8.3.99 🚀 Python-3.11.11 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: task=detect, mode=train, model=yolo11s.pt, data=/content/data.yaml, epochs=60, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=Fa

In [ ]:
# !rm -rf /content/runs/detect/train6

In [ ]:
!zip -r runs.zip /content/runs
#

  adding: content/runs/ (stored 0%)
  adding: content/runs/detect/ (stored 0%)
  adding: content/runs/detect/train/ (stored 0%)
  adding: content/runs/detect/train/PR_curve.png (deflated 21%)
  adding: content/runs/detect/train/args.yaml (deflated 53%)
  adding: content/runs/detect/train/train_batch0.jpg (deflated 7%)
  adding: content/runs/detect/train/weights/ (stored 0%)
  adding: content/runs/detect/train/weights/last.pt (deflated 12%)
  adding: content/runs/detect/train/weights/best.pt (deflated 12%)
  adding: content/runs/detect/train/val_batch0_pred.jpg (deflated 15%)
  adding: content/runs/detect/train/val_batch0_labels.jpg (deflated 15%)
  adding: content/runs/detect/train/train_batch652.jpg (deflated 15%)
  adding: content/runs/detect/train/train_batch650.jpg (deflated 13%)
  adding: content/runs/detect/train/confusion_matrix.png (deflated 37%)
  adding: content/runs/detect/train/train_batch651.jpg (deflated 14%)
  adding: content/runs/detect/train/events.out.tfevents.1743372

In [ ]:
from google.colab import files
# files.download('runs.zip')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from google.colab import files
files.download('/content/runs/detect/train/weights/best.pt')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
!yolo predict \
  model=/content/runs/detect/train/weights/best.pt \
  source=/content/video_keys.mp4 \
  save=True \
  save_txt=True \
  save_conf=True \
  conf=0.2

Ultralytics 8.3.99 🚀 Python-3.11.11 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
Model summary (fused): 72 layers, 3,006,038 parameters, 0 gradients, 8.1 GFLOPs

video 1/1 (frame 1/818) /content/video_keys.mp4: 928x1600 2 House_Keys, 1 Work_Key, 38.6ms
video 1/1 (frame 2/818) /content/video_keys.mp4: 928x1600 2 House_Keys, 1 Work_Key, 19.1ms
video 1/1 (frame 3/818) /content/video_keys.mp4: 928x1600 1 House_Key, 1 Work_Key, 19.1ms
video 1/1 (frame 4/818) /content/video_keys.mp4: 928x1600 1 House_Key, 1 Work_Key, 19.0ms
video 1/1 (frame 5/818) /content/video_keys.mp4: 928x1600 1 House_Key, 1 Work_Key, 19.0ms
video 1/1 (frame 6/818) /content/video_keys.mp4: 928x1600 1 House_Key, 1 Work_Key, 19.0ms
video 1/1 (frame 7/818) /content/video_keys.mp4: 928x1600 1 House_Key, 1 Work_Key, 16.8ms
video 1/1 (frame 8/818) /content/video_keys.mp4: 928x1600 3 House_Keys, 1 Work_Key, 16.9ms
video 1/1 (frame 9/818) /content/video_keys.mp4: 928x1600 3 House_Keys, 1 Work_Key, 16.8ms
video 1/1 (frame 10/818

In [ ]:
# !rm -rf /content/runs/detect/predict*


In [ ]:
!ls /content/runs/detect/predict*


labels	video_keys.avi


In [ ]:
!ls -lt /content/runs/detect/ | head


total 8
drwxr-xr-x 3 root root 4096 Mar 30 23:15 predict
drwxr-xr-x 3 root root 4096 Mar 30 23:14 train


In [ ]:
!ffmpeg -i /content/runs/detect/predict/video_keys.avi -vcodec libx264 /content/video_keys.mp4 -y


ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

In [ ]:
from IPython.display import Video
Video('/content/video_keys.mp4', embed=True)


In [ ]:
import cv2
import os

# Load YOLO prediction video
video_path = '/content/runs/detect/predict/video_keys.mp4'
cap = cv2.VideoCapture(video_path)

# Set up variables for tracking
prev_positions = {'abed_key': None, 'mubeen_key': None}
stationary_counter = {'abed_key': 0, 'mubeen_key': 0}
threshold = 3  # Number of consecutive frames to consider it stopped
movement_tolerance = 10  # Pixel threshold to consider movement

frame_id = 0

while cap.isOpened():
    success, frame = cap.read()
    if not success:
        break

    # Path to YOLO label file for current frame
    label_path = f'/content/runs/detect/predict/labels/frame{frame_id:05d}.txt'
    if os.path.exists(label_path):
        with open(label_path, 'r') as f:
            for line in f.readlines():
                class_id, x_center, y_center, w, h, conf = map(float, line.strip().split())
                x, y = int(x_center * frame.shape[1]), int(y_center * frame.shape[0])

                # Get class name
                class_name = ['abed_key', 'mubeen_key'][int(class_id)]
                prev = prev_positions[class_name]

                if prev is not None:
                    dx = abs(prev[0] - x)
                    dy = abs(prev[1] - y)
                    if dx < movement_tolerance and dy < movement_tolerance:
                        stationary_counter[class_name] += 1
                    else:
                        stationary_counter[class_name] = 0
                prev_positions[class_name] = (x, y)

                # Trigger message if key is stationary for N frames
                if stationary_counter[class_name] == threshold:
                    print(f"🔔 {class_name} has stopped moving!")

    frame_id += 1

cap.release()


In [ ]:
# Create "my_model" folder to store model weights and train results
!mkdir /content/my_model
!cp /content/runs/detect/train/weights/best.pt /content/my_model/my_model.pt
!cp -r /content/runs/detect/train /content/my_model

# Zip into "my_model.zip"
%cd my_model
!zip /content/my_model.zip my_model.pt
!zip -r /content/my_model.zip train
%cd /content

cp: cannot stat '/content/runs/detect/train/weights/best.pt': No such file or directory
/content/my_model
	zip warning: name not matched: my_model.pt

zip error: Nothing to do! (/content/my_model.zip)
  adding: train/ (stored 0%)
  adding: train/args.yaml (deflated 53%)
  adding: train/weights/ (stored 0%)
/content


In [ ]:
# This takes forever for some reason, you can also just download the model from the sidebar
from google.colab import files

files.download('/content/my_model.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>